# StandardHistFactoryPlotsWithCategories
StandardHistFactoryPlotsWithCategories

 This is a standard demo that can be used with any ROOT file
 prepared in the standard way.  You specify:
 - name for input ROOT file
 - name of workspace inside ROOT file that holds model and data
 - name of ModelConfig that specifies details for calculator tools
 - name of dataset

 With default parameters the macro will attempt to run the
 standard hist2workspace example and read the ROOT file
 that it produces.

 The macro will scan through all the categories in a simPdf find the corresponding
 observable.  For each category, it will loop through each of the nuisance parameters
 and plot
 - the data
 - the nominal model (blue)
 - the +Nsigma (red)
 - the -Nsigma (green)

 You can specify how many sigma to vary by changing nSigmaToVary.
 You can also change the signal rate by changing muVal.

 The script produces a lot plots, you can merge them by doing:
```cpp
 gs -q -dNOPAUSE -dBATCH -sDEVICE=pdfwrite -sOutputFile=merged.pdf `ls *pdf`
```




**Author:** Kyle Cranmer  
<i><small>This notebook tutorial was automatically generated with <a href= "https://github.com/root-project/root/blob/master/documentation/doxygen/converttonotebook.py">ROOTBOOK-izer</a> from the macro found in the ROOT repository  on Wednesday, April 17, 2024 at 11:21 AM.</small></i>

In [1]:
%%cpp -d
#include "TFile.h"
#include "TROOT.h"
#include "TCanvas.h"
#include "TList.h"
#include "TMath.h"
#include "TSystem.h"
#include "RooWorkspace.h"
#include "RooAbsData.h"
#include "RooRealVar.h"
#include "RooPlot.h"
#include "RooSimultaneous.h"
#include "RooCategory.h"

#include "RooStats/ModelConfig.h"
#include "RooStats/ProfileInspector.h"

using namespace RooFit;
using namespace RooStats;
using std::cout, std::endl;

 Arguments are defined. 

In [2]:
const char *infile = "";
const char *workspaceName = "combined";
const char *modelConfigName = "ModelConfig";
const char *dataName = "obsData";

In [3]:
double nSigmaToVary = 5.;
double muVal = 0;
bool doFit = false;

-------------------------------------------------------
First part is just to access a user-defined file
or create the standard example file if it doesn't exist

In [4]:
const char *filename = "";
if (!strcmp(infile, "")) {
   filename = "results/example_combined_GaussExample_model.root";
   bool fileExist = !gSystem->AccessPathName(filename); // note opposite return code
                                                        // if file does not exists generate with histfactory
   if (!fileExist) {
      // Normally this would be run on the command line
      cout << "will run standard hist2workspace example" << endl;
      gROOT->ProcessLine(".! prepareHistFactory .");
      gROOT->ProcessLine(".! hist2workspace config/example.xml");
      cout << "\n\n---------------------" << endl;
      cout << "Done creating example input" << endl;
      cout << "---------------------\n\n" << endl;
   }

} else
   filename = infile;

Try to open the file

In [5]:
TFile *file = TFile::Open(filename);

if input file was specified byt not found, quit

In [6]:
if (!file) {
   cout << "StandardRooStatsDemoMacro: Input file " << filename << " is not found" << endl;
   return;
}

-------------------------------------------------------
Tutorial starts here
-------------------------------------------------------

get the workspace out of the file

In [7]:
RooWorkspace *w = (RooWorkspace *)file->Get(workspaceName);
if (!w) {
   cout << "workspace not found" << endl;
   return;
}

get the modelConfig out of the file

In [8]:
ModelConfig *mc = (ModelConfig *)w->obj(modelConfigName);

get the modelConfig out of the file

In [9]:
RooAbsData *data = w->data(dataName);

input_line_84:2:2: warning: 'data' shadows a declaration with the same name in the 'std' namespace; use '::data' to reference this declaration
 RooAbsData *data = w->data(dataName);
 ^


make sure ingredients are found

In [10]:
if (!data || !mc) {
   w->Print();
   cout << "data or ModelConfig was not found" << endl;
   return;
}

input_line_85:2:7: error: reference to 'data' is ambiguous
 if (!data || !mc) {
      ^
input_line_84:2:14: note: candidate found by name lookup is 'data'
 RooAbsData *data = w->data(dataName);
             ^
/usr/include/c++/9/bits/range_access.h:318:5: note: candidate found by name lookup is 'std::data'
    data(initializer_list<_Tp> __il) noexcept
    ^
/usr/include/c++/9/bits/range_access.h:289:5: note: candidate found by name lookup is 'std::data'
    data(_Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:299:5: note: candidate found by name lookup is 'std::data'
    data(const _Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:309:5: note: candidate found by name lookup is 'std::data'
    data(_Tp (&__array)[_Nm]) noexcept
    ^


-------------------------------------------------------
now use the profile inspector

In [11]:
RooRealVar *obs = (RooRealVar *)mc->GetObservables()->first();
TList *list = new TList();

RooRealVar *firstPOI = dynamic_cast<RooRealVar *>(mc->GetParametersOfInterest()->first());

firstPOI->setVal(muVal);

input_line_86:3:1: warning: 'list' shadows a declaration with the same name in the 'std' namespace; use '::list' to reference this declaration
TList *list = new TList();
^


firstPOI->setConstant();

In [12]:
if (doFit) {
   mc->GetPdf()->fitTo(*data);
}

input_line_87:3:25: error: reference to 'data' is ambiguous
   mc->GetPdf()->fitTo(*data);
                        ^
input_line_84:2:14: note: candidate found by name lookup is 'data'
 RooAbsData *data = w->data(dataName);
             ^
/usr/include/c++/9/bits/range_access.h:318:5: note: candidate found by name lookup is 'std::data'
    data(initializer_list<_Tp> __il) noexcept
    ^
/usr/include/c++/9/bits/range_access.h:289:5: note: candidate found by name lookup is 'std::data'
    data(_Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:299:5: note: candidate found by name lookup is 'std::data'
    data(const _Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:309:5: note: candidate found by name lookup is 'std::data'
    data(_Tp (&__array)[_Nm]) noexcept
    ^


-------------------------------------------------------

In [13]:
mc->GetNuisanceParameters()->Print("v");
int nPlotsMax = 1000;
cout << " check expectedData by category" << endl;
RooDataSet *simData = NULL;
RooSimultaneous *simPdf = NULL;
if (strcmp(mc->GetPdf()->ClassName(), "RooSimultaneous") == 0) {
   cout << "Is a simultaneous PDF" << endl;
   simPdf = (RooSimultaneous *)(mc->GetPdf());
} else {
   cout << "Is not a simultaneous PDF" << endl;
}

if (doFit) {
   RooCategory *channelCat = (RooCategory *)(&simPdf->indexCat());
   auto const& catName = channelCat->begin()->first;
   RooAbsPdf *pdftmp = ((RooSimultaneous *)mc->GetPdf())->getPdf(catName.c_str());
   std::unique_ptr<RooArgSet> obstmp{pdftmp->getObservables(*mc->GetObservables())};
   obs = ((RooRealVar *)obstmp->first());
   RooPlot *frame = obs->frame();
   cout << Form("%s==%s::%s", channelCat->GetName(), channelCat->GetName(), catName.c_str()) << endl;
   cout << catName << " " << channelCat->getLabel() << endl;
   data->plotOn(frame, MarkerSize(1),
                Cut(Form("%s==%s::%s", channelCat->GetName(), channelCat->GetName(), catName.c_str())),
                DataError(RooAbsData::None));

   Double_t normCount =
      data->sumEntries(Form("%s==%s::%s", channelCat->GetName(), channelCat->GetName(), catName.c_str()));

   pdftmp->plotOn(frame, LineWidth(2.), Normalization(normCount, RooAbsReal::NumEvent));
   frame->Draw();
   cout << "expected events = " << mc->GetPdf()->expectedEvents(*data->get()) << endl;
   return;
}

int nPlots = 0;
if (!simPdf) {

   for (auto *var : static_range_cast<RooRealVar *>(*mc->GetNuisanceParameters())) {
      RooPlot *frame = obs->frame();
      frame->SetYTitle(var->GetName());
      data->plotOn(frame, MarkerSize(1));
      var->setVal(0);
      mc->GetPdf()->plotOn(frame, LineWidth(1.));
      var->setVal(1);
      mc->GetPdf()->plotOn(frame, LineColor(kRed), LineStyle(kDashed), LineWidth(1));
      var->setVal(-1);
      mc->GetPdf()->plotOn(frame, LineColor(kGreen), LineStyle(kDashed), LineWidth(1));
      list->Add(frame);
      var->setVal(0);
   }

} else {
   RooCategory *channelCat = (RooCategory *)(&simPdf->indexCat());
   for (auto const& tt : *channelCat) {

      if (nPlots == nPlotsMax) {
         break;
      }

      auto const& catName = tt.first;

      cout << "on type " << catName << " " << endl;
      // Get pdf associated with state from simpdf
      RooAbsPdf *pdftmp = simPdf->getPdf(catName.c_str());

      // Generate observables defined by the pdf associated with this state
      std::unique_ptr<RooArgSet> obstmp{pdftmp->getObservables(*mc->GetObservables())};
      //      obstmp->Print();

      obs = ((RooRealVar *)obstmp->first());

      TIter it = mc->GetNuisanceParameters()->createIterator();
      RooRealVar *var = NULL;
      while (nPlots < nPlotsMax && (var = (RooRealVar *)it.Next())) {
         TCanvas *c2 = new TCanvas("c2");
         RooPlot *frame = obs->frame();
         frame->SetName(Form("frame%d", nPlots));
         frame->SetYTitle(var->GetName());

         cout << Form("%s==%s::%s", channelCat->GetName(), channelCat->GetName(), catName.c_str()) << endl;
         cout << catName << " " << channelCat->getLabel() << endl;
         data->plotOn(frame, MarkerSize(1),
                      Cut(Form("%s==%s::%s", channelCat->GetName(), channelCat->GetName(), catName.c_str())),
                      DataError(RooAbsData::None));

         Double_t normCount =
            data->sumEntries(Form("%s==%s::%s", channelCat->GetName(), channelCat->GetName(), catName.c_str()));

         if (strcmp(var->GetName(), "Lumi") == 0) {
            cout << "working on lumi" << endl;
            var->setVal(w->var("nominalLumi")->getVal());
            var->Print();
         } else {
            var->setVal(0);
         }
         // w->allVars().Print("v");
         // mc->GetNuisanceParameters()->Print("v");
         // pdftmp->plotOn(frame,LineWidth(2.));
         // mc->GetPdf()->plotOn(frame,LineWidth(2.),Slice(*channelCat,catName.c_str()),ProjWData(*data));
         // pdftmp->plotOn(frame,LineWidth(2.),Slice(*channelCat,catName.c_str()),ProjWData(*data));
         normCount = pdftmp->expectedEvents(*obs);
         pdftmp->plotOn(frame, LineWidth(2.), Normalization(normCount, RooAbsReal::NumEvent));

         if (strcmp(var->GetName(), "Lumi") == 0) {
            cout << "working on lumi" << endl;
            var->setVal(w->var("nominalLumi")->getVal() + 0.05);
            var->Print();
         } else {
            var->setVal(nSigmaToVary);
         }
         // pdftmp->plotOn(frame,LineColor(kRed),LineStyle(kDashed),LineWidth(2));
         // mc->GetPdf()->plotOn(frame,LineColor(kRed),LineStyle(kDashed),LineWidth(2.),Slice(*channelCat,catName.c_str()),ProjWData(*data));
         // pdftmp->plotOn(frame,LineColor(kRed),LineStyle(kDashed),LineWidth(2.),Slice(*channelCat,catName.c_str()),ProjWData(*data));
         normCount = pdftmp->expectedEvents(*obs);
         pdftmp->plotOn(frame, LineWidth(2.), LineColor(kRed), LineStyle(kDashed),
                        Normalization(normCount, RooAbsReal::NumEvent));

         if (strcmp(var->GetName(), "Lumi") == 0) {
            cout << "working on lumi" << endl;
            var->setVal(w->var("nominalLumi")->getVal() - 0.05);
            var->Print();
         } else {
            var->setVal(-nSigmaToVary);
         }
         // pdftmp->plotOn(frame,LineColor(kGreen),LineStyle(kDashed),LineWidth(2));
         // mc->GetPdf()->plotOn(frame,LineColor(kGreen),LineStyle(kDashed),LineWidth(2),Slice(*channelCat,catName.c_str()),ProjWData(*data));
         // pdftmp->plotOn(frame,LineColor(kGreen),LineStyle(kDashed),LineWidth(2),Slice(*channelCat,catName.c_str()),ProjWData(*data));
         normCount = pdftmp->expectedEvents(*obs);
         pdftmp->plotOn(frame, LineWidth(2.), LineColor(kGreen), LineStyle(kDashed),
                        Normalization(normCount, RooAbsReal::NumEvent));

         // set them back to normal
         if (strcmp(var->GetName(), "Lumi") == 0) {
            cout << "working on lumi" << endl;
            var->setVal(w->var("nominalLumi")->getVal());
            var->Print();
         } else {
            var->setVal(0);
         }

         list->Add(frame);

         // quit making plots
         ++nPlots;

         frame->Draw();
         c2->SaveAs(Form("%s_%s_%s.pdf", catName.c_str(), obs->GetName(), var->GetName()));
         delete c2;
      }
   }
}

input_line_88:23:4: error: reference to 'data' is ambiguous
   data->plotOn(frame, MarkerSize(1),
   ^
input_line_84:2:14: note: candidate found by name lookup is 'data'
 RooAbsData *data = w->data(dataName);
             ^
/usr/include/c++/9/bits/range_access.h:318:5: note: candidate found by name lookup is 'std::data'
    data(initializer_list<_Tp> __il) noexcept
    ^
/usr/include/c++/9/bits/range_access.h:289:5: note: candidate found by name lookup is 'std::data'
    data(_Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:299:5: note: candidate found by name lookup is 'std::data'
    data(const _Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:309:5: note: candidate found by name lookup is 'std::data'
    data(_Tp (&__array)[_Nm]) noexcept
    ^
input_line_88:28:7: error: reference to 'data' is ambiguous
      data->sumEntries(Form("%s==%s::%s", channelCat->GetName(), channelCat->GetNam

-------------------------------------------------------

now make plots

In [14]:
TCanvas *c1 = new TCanvas("c1", "ProfileInspectorDemo", 800, 200);
if (list->GetSize() > 4) {
   double n = list->GetSize();
   int nx = (int)sqrt(n);
   int ny = TMath::CeilNint(n / nx);
   nx = TMath::CeilNint(sqrt(n));
   c1->Divide(ny, nx);
} else
   c1->Divide(list->GetSize());
for (int i = 0; i < list->GetSize(); ++i) {
   c1->cd(i + 1);
   list->At(i)->Draw();
}

input_line_89:3:5: error: reference to 'list' is ambiguous
if (list->GetSize() > 4) {
    ^
input_line_86:3:8: note: candidate found by name lookup is 'list'
TList *list = new TList();
       ^
/usr/include/c++/9/bits/stl_list.h:552:11: note: candidate found by name lookup is 'std::list'
    class list : protected _List_base<_Tp, _Alloc>
          ^
input_line_89:3:5: error: reference to 'list' is ambiguous
if (list->GetSize() > 4) {
    ^
input_line_86:3:8: note: candidate found by name lookup is 'list'
TList *list = new TList();
       ^
/usr/include/c++/9/bits/stl_list.h:552:11: note: candidate found by name lookup is 'std::list'
    class list : protected _List_base<_Tp, _Alloc>
          ^
input_line_89:3:9: error: cannot use arrow operator on a type
if (list->GetSize() > 4) {
        ^
input_line_89:4:15: error: reference to 'list' is ambiguous
   double n = list->GetSize();
              ^
input_line_86:3:8: note: candidate found by name lookup is 'list'
TList *list = new TList(

Draw all canvases 

In [15]:
%jsroot on
gROOT->GetListOfCanvases()->Draw()